In [1]:
#!/usr/bin/env python
# -*- coding: utf-8 -*-

from topogram_client import TopogramAPIClient

from csv import DictReader
import os
import json
import pymongo
#import musicbrainzngs
import arrow
from datetime import datetime
from pymongo import MongoClient
from collections import defaultdict
from dateutil import parser
from datetime import timedelta
import pickle
import time
from slugify import slugify
from fuzzywuzzy import fuzz
import urllib
import math

##SET PATH TO SAVE FILES:
savpath="./bands_dicts/"


In [19]:
#a function to have a range of colors for nodes/edges 
import colorsys
def get_N_HexCol(N=20):

    HSV_tuples = [(x*1.0/N, 0.5, 0.5) for x in xrange(N)]
    hex_out = []
    for rgb in HSV_tuples:
        rgb = map(lambda x: int(x*255),colorsys.hsv_to_rgb(*rgb))
        hex_out.append("".join(map(lambda x: chr(x).encode('hex'),rgb)))
    return hex_out

In [26]:
def create_topogram(title, nodes, edges):

    print "Creating topogram '%s'"%title

    try :
        r = topogram.create_topogram(title)
    except ValueError:
        print '> Topogram already exists'
        r = topogram.get_topogram_by_name(title)
        
    print r
    topogram_ID = r["data"]["_id"]
    print "topogram ID : %s"%topogram_ID

    # get and backup existing nodes and edges
    existing_nodes = topogram.get_nodes(topogram_ID)["data"]
    existing_edges = topogram.get_edges(topogram_ID)["data"]

    # clear existing graph
    if len(existing_nodes):
        topogram.delete_nodes([n["_id"] for n in existing_nodes])
        print "%s nodes deleted"%len(existing_nodes)
    if len(existing_edges):
        topogram.delete_edges([n["_id"] for n in existing_edges])
        print "%s edges deleted"%len(existing_edges)

    r = topogram.create_nodes(topogram_ID, nodes)
    #print r
    print "%s nodes created."%len(r["data"])
    r = topogram.create_edges(topogram_ID, edges)
    print "%s edges created."%len(r["data"])

    #r=topogram.makePublic(topogram_ID)
    print "done. Topogram has been updated. Check it at %s/topograms/%s"%(TOPOGRAM_URL, topogram_ID)



In [13]:
artist={}
artist["name"]="steve-aoki"
artist["mbid"]="a39acc4a-985e-4173-a9ed-f325f2d3bc1c"

with open("../../4_miner/tour_miner/"+slugify(artist["name"]+artist["mbid"])+".obj", 'rb') as handle:
          tempL= pickle.load( handle)
print tempL

{1: {'tourLength': 9, 'tourdist': 8537.241216520675, 'tourYear': 2008, 'tourdistOpt': 9340.712656690901}, 2: {'tourLength': 3, 'tourdist': 3897.598127259958, 'tourYear': 2008, 'tourdistOpt': 3897.598127259958}, 3: {'tourLength': 291, 'tourdist': 925631.7134221339, 'tourYear': 2009, 'tourdistOpt': 89218.09486013964}, 4: {'tourLength': 131, 'tourdist': 356680.719377711, 'tourYear': 2011, 'tourdistOpt': 69523.71811121632}, 'name': u'Steve Aoki', 6: {'tourLength': 355, 'tourdist': 914263.7746566971, 'tourYear': 2012, 'tourdistOpt': 100188.48034786052}, 7: {'tourLength': 188, 'tourdist': 546725.6589293461, 'tourYear': 2014, 'tourdistOpt': 78159.49849836492}, 8: {'tourLength': 102, 'tourdist': 278360.29618725023, 'tourYear': 2015, 'tourdistOpt': 65190.75458792534}, 9: {'tourLength': 235, 'tourdist': 769053.0295231593, 'tourYear': 2016, 'tourdistOpt': 86930.7992358514}, 'totalArtistOptTourDist': 516304.3627186067, 'OptArtistPercent': 86.5401284841919, 'totalArtistTourDist': 3835878.835189679,

In [137]:
###HERE WE BUILD A LABEL OWNERSHIP CRUSHER FACTORIZED
with open("../../4_miner/labels_aliases_TOTAL.obj", 'rb') as handle:
          tempRelAll= pickle.load( handle)
def find_owning_label(label):
    
    labrels=[]
    if "label-relation-list" in tempRelAll[label]["label"] :

        for relat in tempRelAll[label]["label"]["label-relation-list"]:
            if "direction" in relat and relat["direction"] == "backward":
                print tempRelAll[label]["label"]["name"],"OWNED BY",relat["target"]," ",tempRelAll[relat["target"]]["label"]["name"]
                labrels.append(relat["target"])
                rum_and_whisky=""
                while rum_and_whisky != "SELF": 
                    rum_and_whisky=find_owning_label(relat["target"])
                print "ENDED LOOP"
                labrels.remove(relat["target"])
                print "LABRELS",labrels
                #if labrels[0]==relat["target"]:
                 #   break
                
            else:
                pass
            
        
        if not labrels :
            print "TOP OF THE TREE FOR ",tempRelAll[label]["label"]["name"]
            return "SELF"
        else:
            return labrels
                


artist={}
artist["name"]="Steve Aoki"
artist["mbid"]="a39acc4a-985e-4173-a9ed-f325f2d3bc1c"

with open("../../4_miner/release_mbnz/"+artist["name"]+artist["mbid"]+".obj", 'rb') as handle:
          tempRelz= pickle.load( handle)
#print tempRel["release-list"][0]['label-info-list'][0]['label']['id']
#print tempRel["release-list"][0]['release-event-list'][0]["date"]




for release in tempRelz["release-list"]:
    print"---------------------------"
    print release['label-info-list'][0]['label']['id']
    print release['label-info-list'][0]['label']['name']
    print release['release-event-list'][0]["date"]
    
    #print tempRelAll[release['label-info-list'][0]['label']['id']]["label"]
    try:
        result_lab=find_owning_label(release['label-info-list'][0]['label']['id'])
        print "REZLAB",result_lab 
        print"XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX"
    except KeyError as e:
        #print e
        pass

---------------------------
6c690937-c6c3-4c4e-9d3e-c62efa989333
Ultra Records
2012-07-10
Ultra Records OWNED BY f0d2ccb8-a269-491c-bbe3-08bdcd3251b7   Ultra Records, Inc.
TOP OF THE TREE FOR  Ultra Records, Inc.
ENDED LOOP
LABRELS []
TOP OF THE TREE FOR  Ultra Records
REZLAB SELF
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
---------------------------
44510f75-af0c-49b5-ab17-179f38452781
Ministry of Sound (Australia)
2010-05-14
Ministry of Sound (Australia) OWNED BY c48b8ed2-46c5-4e51-9bea-5a37fcd0053b   Ministry of Sound
Ministry of Sound OWNED BY 136021ca-a54d-4451-99c9-6ecf52121b86   Ministry of Sound Recordings Ltd.
Ministry of Sound Recordings Ltd. OWNED BY 9a40374c-c95b-47bc-b353-b2b9728848d3   Sony Music Entertainment UK Limited
Sony Music Entertainment UK Limited OWNED BY b54769e4-b75e-4f60-884a-c4714687bb4c   Sony Music Entertainment
Sony Music Entertainment OWNED BY a57fa9c5-f488-4bae-9eb6-41b734227e90   Sony Corporation of America
TOP OF THE TREE FOR  Sony Corporation of America
ENDED

In [21]:
# setup mongo
client = MongoClient()
db = client["bandstour"]
bandsintown =  db["minedArtists"]

# credentials
TOPOGRAM_URL = "http://localhost:3000"
USER = "gregory.bahde@laposte.net"
PASSWORD = "matrix"

# data
#title = "Foo Fighters bandstour 0.1"
my_nodesdict = {}
my_nodes= []
my_edges = []
my_edgesdict = {}
my_nodesdictGLOBAL={}

#LIVENATION CATALOGUE
liste_salles_LN = json.load(open('./JSON_LIVENATION_VENUE.json'))

liste_salle_parsee_LN={}
for salle in liste_salles_LN:
    if liste_salles_LN[salle]["type"]=="venue":
 
            liste_salle_parsee_LN[slugify(liste_salles_LN[salle]["title"])]={"lat":liste_salles_LN[salle]["position"]["lat"],"lng":liste_salles_LN[salle]["position"]["lng"]}
#print liste_salle_parsee_LN


# date parsing
DATETIME_FORMAT = '%Y-%m-%dT%H:%M:%S'
DATETIME_FORMAT_FOR_MSBNZ ='%Y-%m-%d'

#retrieve trip coords for each artist
dict_coords={}
colors_for_nodes_and_edges = get_N_HexCol()

for artist in db.minedArtists.find({"totalKm": {"$gte": 200000}}) :
 title = artist["name"]   
 if os.path.exists(savpath+slugify(artist["name"]+str(artist["mbid"]))+".obj")==True:
        my_nodesdict = {}
        my_nodesdictList=[]
        print "SKIPPED PROCESSING BUT TAKING INTO ACCOUNT ",artist["name"]
        with open(savpath+slugify(artist["name"]+str(artist["mbid"]))+".obj", 'rb') as handle:
          tempL= pickle.load( handle)
    #print 
        tit=tempL[0].encode("utf-8")
        #edgestop=temp[2]
        my_nodesdictList=tempL[1]
        for node in my_nodesdictList:
            my_nodesdict[node["data"]["id"]]=node

        #print my_nodes
        #pass
 else:
  my_nodesdict = {}
  my_nodes= []
  my_edges = []
  my_nodesdictList=[]
  my_edgesdict = {}
    #colors_for_nodes_and_edges = get_N_HexCol()
    
  print artist["name"]
   #print artist
  dates_coords = []
  dates = artist.get("gigs")
  tours = artist.get("tours")    
  singlegigs = artist.get("singleGigs")
  dateini=0
  touring=0
  tour_indice=0
  tour_counter_for_CO2=1
  tour_counter_for_CO2_lock=0
  tmpOLDgig ={}
  if os.path.exists("../../4_miner/tour_miner/"+slugify(artist["name"]+str(artist["mbid"]))+".obj") == True:
    with open("../../4_miner/tour_miner/"+slugify(artist["name"]+str(artist["mbid"]))+".obj", 'rb') as handle:
                    tempCO2= pickle.load( handle)
    #print tempCO2
    #print tours
    for tour in tours:
        
        ##WE NEED TO MATCH TOUR INDICES OF CO2 SPECS FILES...
     if tour_counter_for_CO2_lock == 1:
        tour_counter_for_CO2+=1
     tour_counter_for_CO2_lock=0
     tour_color = "#"+colors_for_nodes_and_edges[tour_indice % 20]
     #print tour_color
     #print tour
     gig_indice =0
     dates = tour.get("gigs")
     for date in dates:
        #print date.get("datetime")
        venue = date.get("venue")
        latitude = venue.get("latitude")
        longitude = venue.get("longitude")
        #print venue
        ###concat key
        idd= slugify(venue["name"])+str(int(venue["latitude"]))+str(int(venue["longitude"]))
        
        if idd not in my_nodesdict:
            
            node = {
                    "id" : idd,
                    "name" : slugify(venue["name"]),
                    "lat" : float(venue["latitude"]),
                    "lng" : float(venue["longitude"]),
                    "weight" : float(1),
                    "start" : date.get("datetime").isoformat(),
                    "end" : (date.get("datetime")+timedelta(days=1)).isoformat(),
                    "color" : tour_color,
                    "notes" : "name : "+slugify(venue["name"])+"  \nlat : "+str(float(venue["latitude"]))+"  \nlng :"+str(float(venue["longitude"]))+"  \n weight :"+str(1)+"  \nstart : "+str(date.get("datetime").isoformat())+"  \nend : "+str((date.get("datetime")+timedelta(days=1)).isoformat())+"  \ncolor :"+str(tour_color)+"  \n  <a href=\"https://google.com/search?q="+slugify(venue["name"])+"\" target=\"_blank\">"+slugify(venue["name"])+"</a>"
                #+"  \n[search venue named "+slugify(venue["name"])+" on google](https://google.com/search?q="+slugify(venue["name"])+")"
                    }
        else:
                
                node = {
                    "id" : idd,
                    "name" : slugify(venue["name"]),
                    "lat" : float(venue["latitude"]),
                    "lng" : float(venue["longitude"]),
                    "weight" : math.sqrt(float(int(round(float(my_nodesdict[idd]["data"].get("weight"))**2))+1)) ,
                    "start" : my_nodesdict[idd]["data"].get("start"),
                    "end" : (date.get("datetime")+timedelta(days=1)).isoformat(),
                    "color" : tour_color,
                    "notes" : "name : "+slugify(venue["name"])+"  \nlat : "+str(float(venue["latitude"]))+"  \nlng :"+str(float(venue["longitude"]))+"  \n weight :"+str((float(my_nodesdict[idd]["data"].get("weight")))**2+1)+"  \nstart : "+str(my_nodesdict[idd]["data"].get("start"))+"  \nend : "+(date.get("datetime")+timedelta(days=1)).isoformat()+"  \ncolor :"+tour_color+"  \n  <a href=\"https://google.com/search?q="+slugify(venue["name"])+"\" target=\"_blank\"> "+slugify(venue["name"])+" </a>"                    #+"  \n[search venue named "+slugify(venue["name"])+" on google](https://google.com/search?q="+slugify(venue["name"])+")"
                    
                    }
        if dateini == 0:
                dateini =1
        else:
                #print my_nodes[-1]["data"]["id"]
                #print dates[gig_indice-1]["distanceToNextGig"]
                
                
                
                notesE=""
                notesE+="distance : "
                try: 
                    notesE+=str(dates[gig_indice]["distanceToNextGig"])
                except KeyError:
                    notesE+="dates[gig_indice][distanceToNextGig] NOT AVAILABLE"
                notesE+=" km  \n"
                notesE+="source : "
                notesE+=str(my_nodes[-1]["data"]["id"])
                notesE+="  target : "
                notesE+=str(node["id"])
                notesE+="  \ndatesource : "
                notesE+=dates[gig_indice -1]["datetime"].isoformat()
                notesE+="  \ndatetarget : "
                notesE+=dates[gig_indice]["datetime"].isoformat()
                notesE+="  \ngroup: "
                notesE+=str(int(tour_indice)+1)
                #notesE+=
                
                
                #print gig_indice
                edge = {
                    "source" : my_nodes[-1]["data"]["id"],
                    "target" : node["id"],
                    "color" :  tour_color,
                    "notes" : notesE,
                    #"weight" : float(e["weight"]),
                    "start" : dates[gig_indice -1]["datetime"].isoformat(),
                    "end" : dates[gig_indice]["datetime"].isoformat(),
                    "group" : str(tour_counter_for_CO2)
                    
                }
                #print edge
                #ADDING EDGES GROUPS/CO2 HERE
                
                if tour["nbGigs"] > 2:
                    try:
                        if tempCO2[tour_counter_for_CO2]['tourdist'] > 1.25*tempCO2[tour_counter_for_CO2]['tourdistOpt']:
                            
                            edge["group"]+=" DASHED2"
                            edge["notes"]+="  \n tournée grandement optimisable  \nDistance parcourue pendant le tour: "+str(tempCO2[tour_counter_for_CO2]['tourdist'])+" km  \n"
                            edge["notes"]+="Distance recalculée: "+str(tempCO2[tour_counter_for_CO2]['tourdistOpt'])+" km  \n"
                            try:
                                edge["notes"]+="Taux d'optimisation "+str((tempCO2[tour_counter_for_CO2]['tourdist']-tempCO2[tour_counter_for_CO2]['tourdistOpt'])/tempCO2[tour_counter_for_CO2]['tourdist'])+" %"
                            except:
                                print "OUPS 2"
                        elif (tempCO2[tour_counter_for_CO2]['tourdist'] < 1.25*tempCO2[tour_counter_for_CO2]['tourdistOpt']) and (tempCO2[tour_counter_for_CO2]['tourdist'] > 1.1*tempCO2[tour_counter_for_CO2]['tourdistOpt']):
                            
                            edge["group"]+=" DASHED1"
                            edge["notes"]+="  \n  tournée optimisable  \nDistance parcourue pendant le tour: "+str(tempCO2[tour_counter_for_CO2]['tourdist'])+" km  \n"
                            edge["notes"]+="Distance recalculée: "+str(tempCO2[tour_counter_for_CO2]['tourdistOpt'])+" km  \n"
                            try:
                                edge["notes"]+="Taux d'optimisation "+str((tempCO2[tour_counter_for_CO2]['tourdist']-tempCO2[tour_counter_for_CO2]['tourdistOpt'])/tempCO2[tour_counter_for_CO2]['tourdist'])+" %"
                            except:
                                print "OUPS 1"
                        elif tempCO2[tour_counter_for_CO2]['tourdistOpt'] > 1.25*tempCO2[tour_counter_for_CO2]['tourdist']:
                            
                            edge["group"]+=" DASHED-2"
                            edge["notes"]+="  \n tournée déjà grandement optimisée  \nDistance parcourue pendant le tour: "+str(tempCO2[tour_counter_for_CO2]['tourdist'])+" km  \n"
                            edge["notes"]+="Distance recalculée: "+str(tempCO2[tour_counter_for_CO2]['tourdistOpt'])+" km  \n"
                            try:
                                edge["notes"]+="Taux d'optimisation "+str((tempCO2[tour_counter_for_CO2]['tourdist']-tempCO2[tour_counter_for_CO2]['tourdistOpt'])/tempCO2[tour_counter_for_CO2]['tourdist'])+" %"
                            except:
                                print "OUPS -2"
                        elif tempCO2[tour_counter_for_CO2]['tourdistOpt'] < 1.25*tempCO2[tour_counter_for_CO2]['tourdist'] and tempCO2[tour_counter_for_CO2]['tourdistOpt'] > 1.1*tempCO2[tour_counter_for_CO2]['tourdist']:
                            
                            edge["group"]+=" DASHED-1"
                            edge["notes"]+="  \n  tournée déjà optimisée  \nDistance parcourue pendant le tour: "+str(tempCO2[tour_counter_for_CO2]['tourdist'])+" km  \n"
                            edge["notes"]+="Distance recalculée: "+str(tempCO2[tour_counter_for_CO2]['tourdistOpt'])+" km  \n"
                            try:
                                edge["notes"]+="Taux d'optimisation "+str((tempCO2[tour_counter_for_CO2]['tourdist']-tempCO2[tour_counter_for_CO2]['tourdistOpt'])/tempCO2[tour_counter_for_CO2]['tourdist'])+" %"
                            except:
                                print "OUPS -1"
                        
                        else:

                            edge["notes"]+="  \nDistance parcourue pendant le tour: "+str(tempCO2[tour_counter_for_CO2]['tourdist'])+" km  \n"
                        tour_counter_for_CO2_lock=1
                    except KeyError as e:
                        print e
                else:
                    #print "TOUR NON COMPTE ", tour_indice, "//",tour_counter_for_CO2
                    continue
                    
                    
                    
                my_edges.append({ "data" : edge })
        my_nodes.append({ "data" : node })   
        my_nodesdict[node["id"]]= { "data" : node }
        gig_indice+=1
    #print my_nodes
    #print "<=============================================>"
    #print my_nodesdict
    #print "<=============================================>"
    #print my_edges
     tour_indice +=1
        #print "coords",latitude,"/",longitude
    for key, value in my_nodesdict.iteritems():
            my_nodesdictList.append(value)
    
    #ADDING LIVENATION DETECTOR

    for node in my_nodesdictList:
        for salle in liste_salle_parsee_LN:
            if fuzz.partial_ratio( node['data']['name'], salle)>=80:
                #print "ONE HEERE"
                if round(node['data']['lat'],2)==round(liste_salle_parsee_LN[salle]["lat"],2) and round(node['data']['lng'],2)==round(liste_salle_parsee_LN[salle]["lng"],2) :
                    #print "CONFIRMED LIVENATION!"
                    node['data']['color']="#ff0000"
                    node['data']["notes"]+="  \nLivenation venue"
        #if liste_salle_parsee_LN
        
        
    #ADDING EDGES WEIGHT
    terp= map(lambda x : str(sorted([x["data"]["source"],x["data"]["target"]])),my_edges)
    
    #print terp
    from collections import Counter
    c= Counter()
    for ter in terp:
        c[ter]+=1
    #print c
    for edge in my_edges:
        if str(sorted([edge["data"]["source"],edge["data"]["target"]])) not in terp:
            print "BUG!!!!"
        else:
            if edge["data"]["source"] == edge["data"]["target"]:
                #print c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))]
                edge["data"]["notes"]+="  \ncounted "+str(c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))])+"  times"
                edge["data"]["weight"]= float(1)
                #print "a"
            else:
                edge["data"]["notes"]+="  \ncounted "+str(c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))])+"  times"
                edge["data"]["weight"]= float(c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))])
                #print "b"
    #print my_edges

    
    
    
    

    titredugraphe =artist["name"]+"/BETA_0.9"+"  \nDistance totale parcourue par l'artiste: "+str(tempCO2["totalArtistTourDist"])+" km"
    titredugraphe += "  \nDistance calculee par Concorde: "+str(tempCO2["totalArtistOptTourDist"])+" km"
    if  "OptArtistPercent" in tempCO2 :
         rateOpt=0
         rateOpt=float(tempCO2["OptArtistPercent"])
         titredugraphe+="  \nPourcentage d'optimisation global calculee:"+str(rateOpt)+" %"
         if rateOpt > 10: 
             titredugraphe+="  \nMARGE D'OPTIMISATION IMPORTANTE"
         elif rateOpt < -10:
              titredugraphe+="  \nTOURNEE DEJA OPTIMISEE"
         else: 
             titredugraphe+="  \nGLOBALEMENT IDENTIQUE"
         
         
    with open(savpath+slugify(artist["name"]+str(artist["mbid"]))+".obj", 'wb') as handle:
                            pickle.dump([titredugraphe,my_nodesdictList,my_edges], handle, protocol=pickle.HIGHEST_PROTOCOL)    
            
    ###CREATE NODE GLOBAL DICT
           
 for key, value in my_nodesdict.iteritems():
            #print "key",key,"/////",value
            if key in my_nodesdictGLOBAL:
                #print "TROUVE"
                #print "key",key,"/////",value
                #print "GLOBAL",my_nodesdictGLOBAL[key]
                my_nodesdictGLOBAL[key]['data']["weight"]=math.sqrt(my_nodesdictGLOBAL[key]['data']["weight"]**2+my_nodesdict[key]['data']["weight"]**2)
                if time.strptime(my_nodesdictGLOBAL[key]['data']["start"],DATETIME_FORMAT)>time.strptime(my_nodesdict[key]['data']["start"],DATETIME_FORMAT):
                    my_nodesdictGLOBAL[key]['data']["start"]=my_nodesdict[key]['data']["start"]
                if time.strptime(my_nodesdictGLOBAL[key]['data']["end"],DATETIME_FORMAT)<time.strptime(my_nodesdict[key]['data']["end"],DATETIME_FORMAT):
                    my_nodesdictGLOBAL[key]['data']["end"]=my_nodesdict[key]['data']["end"]
                my_nodesdictGLOBAL[key]['data']["notes"]+="  \n"+slugify(artist["name"])
                my_nodesdictGLOBAL[key]['data']["count"]+=int(1)
                #print "GLOBAL2",my_nodesdictGLOBAL[key]
            else:
                my_nodesdictGLOBAL[key]=value
                #print my_nodesdictGLOBAL[key]
                my_nodesdictGLOBAL[key]['data']["notes"]="  \n List of the bands that played in this venue:  \n"+slugify(artist["name"])
                my_nodesdictGLOBAL[key]['data']["count"]=int(1)
for key in my_nodesdictGLOBAL:
    my_nodesdictGLOBAL[key]['data']["notes"]+="  \n TOTAL: "+str(my_nodesdictGLOBAL[key]['data']["count"])+" Bands"
    
    
with open("./my_nodesdictGLOBAL_TEST.obj", 'wb') as handle:
                            pickle.dump(my_nodesdictGLOBAL, handle, protocol=pickle.HIGHEST_PROTOCOL)

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  !!!
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  (həd) p.e.
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  .38 Special
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  10 String Symphony
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  10 Years
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  10cc
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  112
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  12
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  12 Stones
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  12th Planet
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  2 Chainz
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  2 Many DJ's
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  2Cellos
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  3 Doors Down
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  30
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  311
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  3LAU
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  40 oz. To Freedom
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  4th

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Alice Cooper
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Alice Russell
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Alisa Weilerstein
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Alison Wonderland
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Alix Perez
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  All Get Out
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  All That Remains
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  All Them Witches
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  All Time Low
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  All-4-One
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Allah-Las
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Allan Harris
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Alle Farben
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Allen Stone
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Allison Miller
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Aloe Blacc
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Alpha Blondy
SKIPPED PROCESSING BUT 

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Arms and Sleepers
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Arno
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Arno Cost
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Arrested Development
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Arrival
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Art Department
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Art Garfunkel
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Art Of Dying
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Artificial Intelligence
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Artists (Band)
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Arturo Sandoval
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Artwork
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Arty
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  As It Is
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Asaf Avidan
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ash
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ashanti
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ash

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Belinda Carlisle
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bell Biv DeVoe
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bell X1
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bella Sarris
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bellamy Brothers Band
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Belle and Sebastian
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bells
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Belphegor
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Allison
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Folds
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Frost
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Gold
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Hammond
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Harper
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Klock
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Nicky
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Ben Ottewell
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bob Moses
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bob Mould
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bob Schneider Music
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bob Sinclar
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bob Wayne
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bob Weir
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bobaflex
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bobby Brown
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bobby Caldwell
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bobby Long
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Body
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bombino
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bon Iver
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bondax
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bone Thugs-n-Harmony
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bonerama
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Boney James
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Bonfire
SKIPPED PRO

...

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Lone Bellow
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Lowest Pair
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Lumineers
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The M Machine
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Maccabees
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Machine
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Magic Numbers
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Mahones
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Maine
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Manhattan Transfer
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Manhattans
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Mantras
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Marcus King Band
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Marshall Tucker Band
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Martinez Brothers
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Mastersons
SKIPPED PROCESSING BUT TAKING INTO AC

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Temperance Movement
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Temptations
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Temptations Review
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Ten Tenors
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Tenors
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Thrillseekers
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Time
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Toasters
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Tommy Castro Band
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Toxic Avenger
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Travelin' McCoury's
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Trews
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The True Mayhem
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Truth
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Tubes
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  The Turnpike Troubadours
SKIPPED PROCESSING BUT TAKING IN

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tonight Alive
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tony Bennett
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tony Furtado
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tony Hadley
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tony Humphries
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tony Lucca
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tony Orlando
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tony Touch
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tonya Kay
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Too Short
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tool
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Toots & The Maytals
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tori Amos
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tornado Wallace
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Toro Y Moi
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tortoise
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Tortured Soul
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  T

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vibronics
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Viceroy
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vices
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vicetone
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Victor
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Victor Calderone
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Victor Wainwright
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Victor Wooten
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vida
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Video Games Live
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vieux Farka Touré
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vijay Iyer
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Viktor
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Village People
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vince Gill
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vince Neil
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vince Staples
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Vincent
SK

SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Words
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Workshop
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Worthy
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Wreckless Eric
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Wu-Tang Clan
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Wyclef Jean
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Wye Oak
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Wynonna
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Wynton Marsalis
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  X Ambassadors
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  XXX
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Xandria
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Xavier Rudd
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Xibalba
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Xilent
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Xosar
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  Xylouris White
SKIPPED PROCESSING BUT TAKING INTO ACCOUNT  YES
SKIPPED PROCESSING BUT TAKING INTO A

In [ ]:
     with open("./my_nodesdictGLOBAL.obj", 'rb') as handle:
          my_nodesdictGLOBAL= pickle.load( handle)

In [6]:
from itertools import islice

def take(n, iterable):
    "Return first n items of the iterable as a list"
    return list(islice(iterable, n))

print take(5,my_nodesdictGLOBAL.iteritems())

[('ohio-university39-83', {'data': {'count': 1, 'start': '2016-06-10T18:30:00', 'end': '2016-06-11T18:30:00', 'name': 'ohio-university', 'weight': 1.0, 'lat': 39.3268329, 'lng': -83.0063841, 'notes': '  \n List of the bands that played in this venue:  \nled-zepagain  \n TOTAL: 1 Bands', 'id': 'ohio-university39-83', 'color': '#7f3f3f'}}), ('ohio-university39-82', {'data': {'count': 9, 'start': '2008-04-09T19:00:00', 'end': '2015-11-15T19:00:00', 'name': 'ohio-university', 'weight': 3.3784927944829333, 'lat': 39.324921, 'lng': -82.099709, 'notes': '  \n List of the bands that played in this venue:  \nben-folds  \njosh-ritter  \nmachine-gun-kelly  \nray-wylie-hubbard  \nrayland-baxter  \nthe-blind-boys-of-alabama  \ntyler-farr  \nwiz-khalifa  \nzo  \n TOTAL: 9 Bands', 'id': 'ohio-university39-82', 'color': '#5f7f3f'}}), ('tucson-music-hall32-110', {'data': {'count': 35, 'start': '2007-12-17T00:00:00', 'end': '2017-09-15T19:00:00', 'name': 'tucson-music-hall', 'weight': 6.9258925443875565

In [22]:
# credentials
TOPOGRAM_URL = "http://localhost:3000"
USER = "gregory.bahde@laposte.net"
PASSWORD = "matrix"

In [5]:
print len(my_nodesdictGLOBAL)

NameError: name 'my_nodesdictGLOBAL' is not defined

In [23]:
# connect to the topogram instance (pass debug=True params for more info )
topogram = TopogramAPIClient(TOPOGRAM_URL) #, debug=True)

# create a new user
try :
    topogram.create_user(USER, PASSWORD)
except ValueError:
    print "> User has already been created."

# login a new user if needed
resp_user_login = topogram.user_login(USER, PASSWORD)
print resp_user_login

assert(resp_user_login["status"] == "success")
assert(resp_user_login["status_code"] == 200)


{u'status': u'success', 'status_code': 200, u'data': {u'authToken': u'TacGxX-EEummobGjmmMwWgx-iK-cJRzP83mITwJWBN2', u'userId': u'apyw7AfhAGbEHigJw'}}


In [27]:
###IMPORT ALL THE BANDS GRAPHS

nodestop=[]
edgestop=[]
tit=[]
import glob, os

print os.getcwd()

for subdir, dirs, files in os.walk(savpath): 
 for file in files:
  if file.endswith('.obj') == True:
    #print file
    with open(os.path.join(subdir, file), 'rb') as handle:
          temp= pickle.load( handle)
    #print temp 
    tit=temp[0].encode("utf-8")
    edgestop=temp[2]
    nodestop=temp[1]
    #print edgestop
    #for edge in edgestop:
    #    assert edge["data
    while True:
        try:
    #        print tit
            create_topogram(tit, nodestop, edgestop)
            
        except TypeError:
            continue
        
        break
print 'DONE'
        

ERROR:topogram-client:500 - Error : A topogram with the same name already exists


/home/goonieb/gitrep/bandstour/5_visualizer/topogram-api-clientFOR_TOPO_FROM_BANDSTOUR
Creating topogram 'The Real McKenzies/BETA_0.9  
Distance totale parcourue par l'artiste: 180910.931868 km  
Distance calculee par Concorde: 155838.456882 km  
Pourcentage d'optimisation global calculee:13.8590159959 %  
MARGE D'OPTIMISATION IMPORTANTE'
> Topogram already exists
{u'status': u'success', 'status_code': 200, u'data': {u'sharedPublic': False, u'title': u"The Real McKenzies/BETA_0.9  \nDistance totale parcourue par l'artiste: 180910.931868 km  \nDistance calculee par Concorde: 155838.456882 km  \nPourcentage d'optimisation global calculee:13.8590159959 %  \nMARGE D'OPTIMISATION IMPORTANTE", u'userId': u'apyw7AfhAGbEHigJw', u'_id': u'39iqjDJHzmZmkWR2Q', u'slug': u'the-real-mckenziesbeta_09-distance-totale-parcourue-par-lartiste-180910931868-km-distance-calculee-par-concorde-155838456882-km-pourcentage-doptimisation-global-calculee138590159959-marge-doptimisation-importante', u'createdAt': 

ERROR:topogram-client:500 - Error : A topogram with the same name already exists


> Topogram already exists
{u'status': u'success', 'status_code': 200, u'data': {u'sharedPublic': False, u'title': u"Killer Queen/BETA_0.9  \nDistance totale parcourue par l'artiste: 66035.1567652 km  \nDistance calculee par Concorde: 61983.6750612 km  \nPourcentage d'optimisation global calculee:6.1353404799 %  \nGLOBALEMENT IDENTIQUE", u'userId': u'apyw7AfhAGbEHigJw', u'_id': u'oGFhe45pfSKAqETJ7', u'slug': u'killer-queenbeta_09-distance-totale-parcourue-par-lartiste-660351567652-km-distance-calculee-par-concorde-619836750612-km-pourcentage-doptimisation-global-calculee61353404799-globalement-identique', u'createdAt': u'2019-10-06T07:05:52.527Z'}, u'statusCode': 200}
topogram ID : oGFhe45pfSKAqETJ7


ERROR:topogram-client:500 - Error : A topogram with the same name already exists


...

ERROR:topogram-client:500 - Error : A topogram with the same name already exists


> Topogram already exists
{u'status': u'success', 'status_code': 200, u'data': {u'sharedPublic': False, u'title': u"Anthrax/BETA_0.9  \nDistance totale parcourue par l'artiste: 383971.386187 km  \nDistance calculee par Concorde: 340623.743336 km  \nPourcentage d'optimisation global calculee:11.2892898821 %  \nMARGE D'OPTIMISATION IMPORTANTE", u'userId': u'apyw7AfhAGbEHigJw', u'_id': u'ud2Lkrjw9aGhzWXDZ', u'slug': u'anthraxbeta_09-distance-totale-parcourue-par-lartiste-383971386187-km-distance-calculee-par-concorde-340623743336-km-pourcentage-doptimisation-global-calculee112892898821-marge-doptimisation-importante', u'createdAt': u'2019-10-06T23:52:58.537Z'}, u'statusCode': 200}
topogram ID : ud2Lkrjw9aGhzWXDZ
432 nodes created.
495 edges created.
done. Topogram has been updated. Check it at http://localhost:3000/topograms/ud2Lkrjw9aGhzWXDZ
Creating topogram 'Terror/BETA_0.9  
Distance totale parcourue par l'artiste: 903381.610131 km  
Distance calculee par Concorde: 754625.252512 km  


ERROR:topogram-client:500 - Error : A topogram with the same name already exists


{u'status': u'success', 'status_code': 200, u'data': u'SJukf6EpJjCaW22Ec', u'statusCode': 201}
Creating topogram 'Terror/BETA_0.9  
Distance totale parcourue par l'artiste: 903381.610131 km  
Distance calculee par Concorde: 754625.252512 km  
Pourcentage d'optimisation global calculee:16.466613439 %  
MARGE D'OPTIMISATION IMPORTANTE'
> Topogram already exists
{u'status': u'success', 'status_code': 200, u'data': {u'sharedPublic': False, u'title': u"Terror/BETA_0.9  \nDistance totale parcourue par l'artiste: 903381.610131 km  \nDistance calculee par Concorde: 754625.252512 km  \nPourcentage d'optimisation global calculee:16.466613439 %  \nMARGE D'OPTIMISATION IMPORTANTE", u'userId': u'apyw7AfhAGbEHigJw', u'_id': u'SJukf6EpJjCaW22Ec', u'slug': u'terrorbeta_09-distance-totale-parcourue-par-lartiste-903381610131-km-distance-calculee-par-concorde-754625252512-km-pourcentage-doptimisation-global-calculee16466613439-marge-doptimisation-importante', u'createdAt': u'2019-10-06T23:54:07.168Z'}, u

ValueError: No JSON object could be decoded

In [50]:
###IMPORT THE GLOBAL VENUE  GRAPH
my_nodesdictList=[]
nodestopo=[]
edgestopo=[]
with open("./my_nodesdictGLOBAL.obj", 'rb') as handle:
          my_nodesdictGLOBAL= pickle.load( handle)
        
for key, value in my_nodesdictGLOBAL.iteritems():
            my_nodesdictGLOBAL[key]["data"].pop('count')
        
for key, value in my_nodesdictGLOBAL.iteritems():
            my_nodesdictList.append(value)
        
nodestopo=sorted(my_nodesdictList, key= lambda (v) : v['data']['weight'], reverse=True)[:5000]
print len(nodestopo)



title="global venue graph /BETA 0.6"

while True:
        try:
            print nodestopo
            create_topogram(title, nodestopo, edgestopo)
        
        except TypeError:
            continue
        break
        

ERROR:topogram-client:500 - Error : A topogram with the same name already exists
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


5000 nodes deleted
5000 nodes created.


ValueError: No JSON object could be decoded

In [14]:
with open("./bands_dicts/the-real-mckenzies01612542-01ec-4fc4-a9ad-b6a6e33f11d7.obj", 'rb') as handle:
          DEBUG= pickle.load( handle)


In [18]:
print DEBUG[:2]


[u"The Real McKenzies/BETA_0.8  \nDistance totale parcourue par l'artiste: 180691.650535 km  \nDistance calculee par Concorde: 156448.795249 km  \nPourcentage d'optimisation global calculee:13.4166992303 %  \nMARGE D'OPTIMISATION IMPORTANTE", [{'data': {'end': '2015-03-27T20:30:00', 'name': 'the-horseshoe-tavern', 'weight': 1.0, 'color': '#7f663f', 'notes': 'name : the-horseshoe-tavern  \nlat : 43.6490438  \nlng :-79.395913  \n weight :1  \nstart : 2015-03-26T20:30:00  \nend : 2015-03-27T20:30:00  \ncolor :#7f663f  \n  <a href="https://google.com/search?q=the-horseshoe-tavern" target="_blank">the-horseshoe-tavern</a>', 'start': '2015-03-26T20:30:00', 'lat': 43.6490438, 'lng': -79.395913, 'id': 'the-horseshoe-tavern43-79'}}, {'data': {'end': '2012-05-09T20:00:00', 'name': 'the-pyramid-cabaret', 'weight': 1.0, 'color': '#723f7f', 'notes': 'name : the-pyramid-cabaret  \nlat : 49.890735  \nlng :-97.137711  \n weight :1  \nstart : 2012-05-08T20:00:00  \nend : 2012-05-09T20:00:00  \ncolor :#